In [3]:
import torch
import pandas as pd
from sklearn.model_selection import train_test_split
from optuna.integration import PyTorchLightningPruningCallback
from pytorch_lightning.loggers import NeptuneLogger
from neptune.new.types import File
import pytorch_lightning as pl
import uuid
import os 



from dataset import extract_users_movies_ratings_lists, TripletDataset, save_predictions

RANDOM_STATE = 42
BATCH_SIZE = 256
DATA_DIR = '../data'


MAX_EPOCHS = 20
DIR_RESULTS = '/cluster/scratch/piattigi/CIL/res_optuna/'
EXPERIMENT_NAME = 'NCF_distribution calibration'
EXPERIMENT_NAME+='-'+str(uuid.uuid4())[:8]
N_OPTUNA_TRIALS = 250
DEBUG = False
NUM_GPUS = 6

NUM_WORKERS_LOADER = 4

os.makedirs(DIR_RESULTS+EXPERIMENT_NAME)



model_params = {'embedding_size': 43, 'hidden_size': 117, 'alpha': 0.30184561739442606, 'sigma_prior': 0.5280354660742225, 'distance_0_to_3': 0.845472089209157, 'distance_3_to_2': 1.0123683337747076, 'distance_2_to_1': 0.12520765022811642, 'distance_0_to_4': 0.24389896700863054, 'distance_4_to_5': 1.9232424230681977, 'p_dropout': 0.14010135653155792, 
'weight_decay': 7.594599314482437e-05, 'scaling': 2.5967376547477308}


#Data source and split into val and train
data_pd = pd.read_csv(DATA_DIR+'/data_train.csv')
train_pd, val_pd = train_test_split(data_pd, train_size=0.9, random_state=RANDOM_STATE)
users_val, movies_val, ratings_val = extract_users_movies_ratings_lists(val_pd)
d_val= TripletDataset(users_val, movies_val, ratings_val, is_test_dataset=True)
val_dataloader = torch.utils.data.DataLoader(d_val, batch_size=BATCH_SIZE, drop_last=False, shuffle=False, num_workers=NUM_WORKERS_LOADER)



In [4]:
from model import NCFDistribution as Model

model = Model.load_from_checkpoint('./end_training.ckpt', **model_params)
trainer = pl.Trainer()


/home/gio/.local/lib/python3.9/site-packages/pytorch_lightning/loops/utilities.py:91: PossibleUserWarning: `max_epochs` was not set. Setting it to 1000 epochs. To train without an epoch limit, set `max_epochs=-1`.
  rank_zero_warn(
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


In [6]:
predictions = trainer.predict(model, dataloaders=val_dataloader)

yhat = torch.concat(predictions)


Predicting DataLoader 0: 100%|██████████| 460/460 [00:02<00:00, 161.06it/s]


array([3.3975146, 3.7328858, 4.021783 , ..., 3.7365675, 3.9040294,
       2.721177 ], dtype=float32)

In [13]:
import plotly.express as px

fig = px.scatter(x=yhat.cpu().numpy(), y=ratings_val)
fig.show()

In [20]:
ratings_val

array([1, 3, 3, ..., 1, 1, 0])

In [30]:
fig = px.histogram(yhat.cpu().numpy()[ratings_val==2])
fig.show()